In [46]:
import os
import folium
import numpy as np

print(folium.__version__)

0.11.0


In [12]:
import json
import requests

url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
us_states = f'{url}/us-states.json'

atx_zip_codes = 'dashapp/atx_zips_coords_ordered.json'
with open(atx_zip_codes) as f:
    map_datax = json.load(f)
geo_json_data = map_datax

#geo_json_data = json.loads(requests.get(atx_zip_codes).text)

In [16]:
m = folium.Map([30.2672, -97.7431], zoom_start=9)

folium.GeoJson(geo_json_data).add_to(m)

m

In [15]:
m = folium.Map([43, -100], zoom_start=4)

folium.GeoJson(atx_zip_codes).add_to(m)

m

In [17]:
import geopandas

gdf = geopandas.read_file(atx_zip_codes)

m = folium.Map([30.2672, -97.7431], zoom_start=9)

folium.GeoJson(
    gdf,
).add_to(m)

m

In [18]:
m = folium.Map([30.2672, -97.7431], zoom_start=9)

folium.GeoJson(
    geo_json_data,
    style_function=lambda feature: {
        'fillColor': '#ffff00',
        'color': 'black',
        'weight': 2,
        'dashArray': '5, 5'
    }
).add_to(m)

m

In [22]:
m = folium.Map([30.2672, -97.7431], zoom_start=9)

folium.GeoJson(
    geo_json_data,
    style_function=lambda feature: {
        'fillColor': 'green' if '2' in feature['properties']['ZCTA5CE10'].lower() else '#ffff00',
        'color': 'black',
        'weight': 2,
        'dashArray': '5, 5'
    }
).add_to(m)

m

In [24]:
import pandas as pd


atx_stats_file = 'dashapp/atxdata.csv'
atx_stats = pd.read_csv(atx_stats_file)

atx_stats.head(5)


Zip Code  Total population  Under 5 years 5 to 9 years 10 to 14 years  \
0     78610             32692           2475         2740           2286   
1     78617             27900           2252         2401           2490   
2     78653             20822           1824         2222           1702   
3     78660             85450           6171         6238           6966   
4     78701              7875             22            -             55   

   15 to 19 years  20 to 24 years  25 to 34 years  35 to 44 years  \
0            2205            1905            5074            5304   
1            3034            2109            4057            4709   
2            1374            1030            3241            3337   
3            6186            3847           14429           14724   
4              47             667            3099            1028   

   45 to 54 years  ...  1.51 or more  Less than $50,000  $50,000 to $99,999  \
0            3763  ...           118                229                 542   
1            3338  ...           210                775                1054   
2            2825  ...            64                344                 414   
3           12286  ...            85               1047                 620   
4             910  ...            66                  -                   3   

   $100,000 to $149,999.1 $150,000 to $199,999.1  $200,000 to $299,999  \
0                     787                   1902                3532.0   
1                    1384                   1014                 543.0   
2                    1347                   1617                 984.0   
3                    3367                   5871                8474.0   
4                      42                     78                  97.0   

   $300,000 to $499,999  $500,000 to $999,999  $1,000,000 or more  \
0                  1393                   295                  15   
1                   103                   176                   -   
2                   386                    40                  23   
3                  1792                   183                  19   
4                   687                   513                 141   

   $2,000,000 or more  
0                  79  
1                   -  
2                  55  
3                 113  
4                 141  

[5 rows x 129 columns]

In [37]:
atx_stats['Zip Code'] = atx_stats['Zip Code'].astype(str)

In [33]:
from branca.colormap import linear

colormap = linear.YlGn_09.scale(
    atx_stats['Total population'].min(),
    atx_stats['Total population'].max())

print(colormap(25000))

colormap

#cceb9dff


In [25]:
color_key = {'C3':'#3b4994', 
             'B3':'#8c62aa',
             'A3':'#be64ac', 
             'C2':'#5698b9', 
             'B2':'#a5add3',
             'A2':'#dfb0d6',
             'C1':'#5ac8c8', 
             'B1':'#ace4e4',
             'A1':'#e8e8e8'}
print(color_key)

{'C3': '#3b4994', 'B3': '#8c62aa', 'A3': '#be64ac', 'C2': '#5698b9', 'B2': '#a5add3', 'A2': '#dfb0d6', 'C1': '#5ac8c8', 'B1': '#ace4e4', 'A1': '#e8e8e8'}


In [39]:
pop_dict = atx_stats.set_index('Zip Code')['Total population']

pop_dict['78723']

33170

In [40]:
female_dict = atx_stats.set_index('Zip Code')['Female']

female_dict['78723']

16869

In [51]:
def determine_bivariate_choropleth_color(zipcode, stat1, stat2):
    # Define the labels to be used in defining the color of the 3x3 matrix
    labels_s1 = ['A', 'B', 'C'] # Green tone C1 is valueable land, not valuable building
    labels_s2 = ['1', '2', '3'] # Pink tone A3 is valuaeable building, not valuable land

    # Define percentile for dividing by 3 (33.33)
    pct = 100 / 3

    # Create the breakpoints for the two columns, land and building
    bp_s1 = np.percentile(atx_stats[stat1], [pct, 100 - pct], axis=0)

    bp_s2 = np.percentile(atx_stats[stat2], [pct, 100 - pct], axis=0)

    # Bin the land assessments
    stat1_val = atx_stats.loc[atx_stats['Zip Code'] == zipcode, stat1].iloc[0]
    if stat1_val > 0 and stat1_val < bp_s1[0]:
        stat1_label = labels_s1[0]
    elif stat1_val >= bp_s1[0] and bp_s1[0] < bp_s1[1]:
        stat1_label = labels_s1[1]
    else:
        stat1_label = labels_s1[2]
#    stat1_label = pd.cut(stat1_val, [0, bp_s1[0], bp_s1[1]:, np.inf], right=False, labels=labels_s1)

    # Bin the building assessments
    stat2_val = atx_stats.loc[atx_stats['Zip Code'] == zipcode, stat2].iloc[0]
    if stat2_val > 0 and stat2_val < bp_s2[0]:
        stat2_label = labels_s2[0]
    elif stat2_val >= bp_s2[0] and bp_s2[0] < bp_s2[1]:
        stat2_label = labels_s2[1]
    else:
        stat2_label = labels_s2[2]
 #   stat2_label = pd.cut(stat2_val, [0, bp_s2[0], bp_s2[1], np.inf], right=False, labels=labels_s2)

    # Concatenate the land and building labels
    color = stat1_label + stat2_label
    
    return color_key[color]

In [41]:
m = folium.Map([30.2672, -97.7431], zoom_start=9)

folium.GeoJson(
    geo_json_data,
    name='population',
    style_function=lambda feature: {
        'fillColor': colormap(pop_dict[feature['properties']['ZCTA5CE10']]),
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.9,
    }
).add_to(m)

folium.LayerControl().add_to(m)

m

In [52]:
m = folium.Map([30.2672, -97.7431], zoom_start=9)

folium.GeoJson(
    geo_json_data,
    name='population',
    style_function=lambda feature: {
        'fillColor': determine_bivariate_choropleth_color(feature['properties']['ZCTA5CE10'],'Total population','Female'),
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.9,
    }
).add_to(m)

folium.LayerControl().add_to(m)

m

In [57]:
atx_stats = atx_stats.replace('-',0)
#atx_stats = atx_stats.astype(int)
atx_stats['Zip Code'] = atx_stats['Zip Code'].astype(str)
atx_stats['Asian alone']

0      535
1      433
2      335
3     7743
4      520
5      431
6     1653
7     1429
8     4884
9      185
10     188
11     705
12      63
13      88
14    2611
15    5016
16    1768
17    2684
18     414
19    2198
20    2056
21    1064
22     475
23    1389
24     338
25     482
26    1437
27    1991
28    2253
29       0
30     425
31    1607
32    2106
33     456
34    2242
35    3555
36    5029
37     989
38     354
39    3495
40    2870
41     382
42     763
43    2787
44    4465
Name: Asian alone, dtype: object

In [63]:
pd.options.display.max_rows = 999
pd.options.display.max_columns = 999
#atx_stats.dtypes
atx_stats

Zip Code  Total population  Under 5 years 5 to 9 years 10 to 14 years  \
0     78610             32692           2475         2740           2286   
1     78617             27900           2252         2401           2490   
2     78653             20822           1824         2222           1702   
3     78660             85450           6171         6238           6966   
4     78701              7875             22            0             55   
5     78702             22876           1313         1453            872   
6     78703             20788           1370         1186           1086   
7     78704             47158           2546         2013           1694   
8     78705             33075            229          241            187   
9     78721             12447            632          742            706   
10    78722              7254            465          363            181   
11    78723             33170           2517         2403           2054   
12    78724             24833           2511         2537           2400   
13    78725              7517            444          632            567   
14    78726             14610            830          854           1287   
15    78727             28999           2020         1202            960   
16    78728             21245           1613         1283            919   
17    78729             29434           2128         1629           1305   
18    78730              8933            312          538            748   
19    78731             27447           1589         1394           1415   
20    78732             17762           1165         1650           2519   
21    78733              8754            686          798            757   
22    78734             18722           1020          999           1373   
23    78735             17919           1164         1362           1093   
24    78736              8199            448          633            446   
25    78737             15879           1073         1175           1442   
26    78738             15746            590         1227           1738   
27    78739             20191           1520         2439           1850   
28    78741             52307           3259         2436           2512   
29    78742               517             15           15              0   
30    78744             48432           4110         4452           4215   
31    78745             62220           3797         3205           2587   
32    78746             28268           1188         2092           2441   
33    78747             20954           1701         1499           1552   
34    78748             49142           3611         2655           2422   
35    78749             37453           2538         2207           2169   
36    78750             30758           1645         2201           2237   
37    78751             14949            628          338            350   
38    78752             20302           1663         1680           1142   
39    78753             58693           5046         4349           3972   
40    78754             23858           2534         1616           1547   
41    78756              8377            428          252            346   
42    78757             24059           1858         1195           1103   
43    78758             46618           3849         3026           2106   
44    78759             41847           2378         2107           1868   

    15 to 19 years  20 to 24 years  25 to 34 years  35 to 44 years  \
0             2205            1905            5074            5304   
1             3034            2109            4057            4709   
2             1374            1030            3241            3337   
3             6186            3847           14429           14724   
4               47             667            3099            1028   
5              999            1533            6140            3664   
6              6

In [64]:
atx_stats = atx_stats.drop('Homeowner vacancy rate', 1)

In [65]:
atx_stats = atx_stats.drop('Rental vacancy rate', 1)

In [67]:
atx_stats.shape

(45, 127)

In [70]:
atx_stats = atx_stats.astype(str)

In [71]:
atx_stats = atx_stats.astype(int)

ValueError: invalid literal for int() with base 10: '11585.0'